# Peer-Graded Assignment IBM
## Segmenting & Clustering Neighbourhoods in Tonronto Canada
### Basic Requirements:
1. Create New Notebook 
2. to scrape the following Wikipedia page, https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M, in order to obtain the data that is in the table of postal codes and to transform the data into a pandas dataframe 
3. To create the above dataframe
4. Submit a link to your Notebook on your Github repository

In [202]:
import sys
!{sys.executable} -m pip install geocoder
!{sys.executable} -m pip install folium
import geocoder

from bs4 import BeautifulSoup
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json # library to handle JSON files
#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
# import k-means from clustering stage
from sklearn.cluster import KMeans
from sklearn.datasets.samples_generator import make_blobs
#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library
from bs4 import BeautifulSoup
import lxml

### Download & Explore Data

In [203]:
# download url data from internet
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
get_source = requests.get(url).text
#Scrape data
soup = BeautifulSoup(get_source, 'html5lib') 
table = soup.find('table', attrs = {'class':'wikitable sortable'})

### Data Elaboration

In [204]:
#Find all items
rows=table.findAll()
rows

[<tbody><tr>
 <th>Postcode</th>
 <th>Borough</th>
 <th>Neighbourhood
 </th></tr>
 <tr>
 <td>M1A</td>
 <td>Not assigned</td>
 <td>Not assigned
 </td></tr>
 <tr>
 <td>M2A</td>
 <td>Not assigned</td>
 <td>Not assigned
 </td></tr>
 <tr>
 <td>M3A</td>
 <td><a href="/wiki/North_York" title="North York">North York</a></td>
 <td><a href="/wiki/Parkwoods" title="Parkwoods">Parkwoods</a>
 </td></tr>
 <tr>
 <td>M4A</td>
 <td><a href="/wiki/North_York" title="North York">North York</a></td>
 <td><a href="/wiki/Victoria_Village" title="Victoria Village">Victoria Village</a>
 </td></tr>
 <tr>
 <td>M5A</td>
 <td><a href="/wiki/Downtown_Toronto" title="Downtown Toronto">Downtown Toronto</a></td>
 <td><a href="/wiki/Regent_Park" title="Regent Park">Harbourfront</a>
 </td></tr>
 <tr>
 <td>M6A</td>
 <td><a href="/wiki/North_York" title="North York">North York</a></td>
 <td><a href="/wiki/Lawrence_Heights" title="Lawrence Heights">Lawrence Heights</a>
 </td></tr>
 <tr>
 <td>M6A</td>
 <td><a href="/wiki/No

In [205]:
# rows show to check more symbols
rows = table.findAll('tr')
rows=rows[0:len(rows)]
rows

[<tr>
 <th>Postcode</th>
 <th>Borough</th>
 <th>Neighbourhood
 </th></tr>, <tr>
 <td>M1A</td>
 <td>Not assigned</td>
 <td>Not assigned
 </td></tr>, <tr>
 <td>M2A</td>
 <td>Not assigned</td>
 <td>Not assigned
 </td></tr>, <tr>
 <td>M3A</td>
 <td><a href="/wiki/North_York" title="North York">North York</a></td>
 <td><a href="/wiki/Parkwoods" title="Parkwoods">Parkwoods</a>
 </td></tr>, <tr>
 <td>M4A</td>
 <td><a href="/wiki/North_York" title="North York">North York</a></td>
 <td><a href="/wiki/Victoria_Village" title="Victoria Village">Victoria Village</a>
 </td></tr>, <tr>
 <td>M5A</td>
 <td><a href="/wiki/Downtown_Toronto" title="Downtown Toronto">Downtown Toronto</a></td>
 <td><a href="/wiki/Regent_Park" title="Regent Park">Harbourfront</a>
 </td></tr>, <tr>
 <td>M6A</td>
 <td><a href="/wiki/North_York" title="North York">North York</a></td>
 <td><a href="/wiki/Lawrence_Heights" title="Lawrence Heights">Lawrence Heights</a>
 </td></tr>, <tr>
 <td>M6A</td>
 <td><a href="/wiki/North_Yor

In [206]:
# rows to check more symbols
rows = table.findAll('td')
rows=rows[0:len(rows)]
rows

[<td>M1A</td>, <td>Not assigned</td>, <td>Not assigned
 </td>, <td>M2A</td>, <td>Not assigned</td>, <td>Not assigned
 </td>, <td>M3A</td>, <td><a href="/wiki/North_York" title="North York">North York</a></td>, <td><a href="/wiki/Parkwoods" title="Parkwoods">Parkwoods</a>
 </td>, <td>M4A</td>, <td><a href="/wiki/North_York" title="North York">North York</a></td>, <td><a href="/wiki/Victoria_Village" title="Victoria Village">Victoria Village</a>
 </td>, <td>M5A</td>, <td><a href="/wiki/Downtown_Toronto" title="Downtown Toronto">Downtown Toronto</a></td>, <td><a href="/wiki/Regent_Park" title="Regent Park">Harbourfront</a>
 </td>, <td>M6A</td>, <td><a href="/wiki/North_York" title="North York">North York</a></td>, <td><a href="/wiki/Lawrence_Heights" title="Lawrence Heights">Lawrence Heights</a>
 </td>, <td>M6A</td>, <td><a href="/wiki/North_York" title="North York">North York</a></td>, <td><a href="/wiki/Lawrence_Manor" title="Lawrence Manor">Lawrence Manor</a>
 </td>, <td>M7A</td>, <td>

In [207]:
# solve headers
headers=table.findAll('th')
for i, head in enumerate(headers): headers[i]=str(headers[i]).replace("<th>","").replace("</th>","").replace("\n","")
headers

['Postcode', 'Borough', 'Neighbourhood']

In [208]:
# solve symbols in rows
rows = table.find_all('tr')
data = []
for row in rows:
    td=[]
    for t in row.find_all('td'):
        td.append(t.text.strip())
    data.append(td)

In [209]:
# Create data frame in rows
df_rows = pd.DataFrame(rows)
df_rows.head()

0
0  <tr>
<th>Postcode</th>
<th>Borough</th>
<th>Ne...
1  <tr>
<td>M1A</td>
<td>Not assigned</td>
<td>No...
2  <tr>
<td>M2A</td>
<td>Not assigned</td>
<td>No...
3  <tr>
<td>M3A</td>
<td><a href="/wiki/North_Yor...
4  <tr>
<td>M4A</td>
<td><a href="/wiki/North_Yor...

In [210]:
# skips symbols in rows
for i, row in enumerate(rows): rows[i] = str(rows[i]).replace("\n</td></tr>","").replace("<tr>\n<td>","")

In [211]:
# set Dataframe into Columns
df = pd.DataFrame(data, columns=['PostalCode', 'Borough', 'Neighbourhood'])
df.head()

PostalCode       Borough     Neighbourhood
0       None          None              None
1        M1A  Not assigned      Not assigned
2        M2A  Not assigned      Not assigned
3        M3A    North York         Parkwoods
4        M4A    North York  Victoria Village

In [212]:
# solve "Not assigned"
df = df[~df['Borough'].isnull()]

df.drop(df[df.Borough == 'Not assigned'].index, inplace=True)
df.reset_index(drop=True, inplace=True)
df['Neighbourhood'].replace('Not assigned',df['Borough'],inplace=True)

df_a = df

df_a

PostalCode           Borough  \
0          M3A        North York   
1          M4A        North York   
2          M5A  Downtown Toronto   
3          M6A        North York   
4          M6A        North York   
5          M7A  Downtown Toronto   
6          M9A      Queen's Park   
7          M1B       Scarborough   
8          M1B       Scarborough   
9          M3B        North York   
10         M4B         East York   
11         M4B         East York   
12         M5B  Downtown Toronto   
13         M5B  Downtown Toronto   
14         M6B        North York   
15         M9B         Etobicoke   
16         M9B         Etobicoke   
17         M9B         Etobicoke   
18         M9B         Etobicoke   
19         M9B         Etobicoke   
20         M1C       Scarborough   
21         M1C       Scarborough   
22         M1C       Scarborough   
23         M3C        North York   
24         M3C        North York   
25         M4C         East York   
26         M5C  Downtown Toronto   
27         M6C              York   
28         M9C         Etobicoke   
29         M9C         Etobicoke   
30         M9C         Etobicoke   
31         M9C         Etobicoke   
32         M1E       Scarborough   
33         M1E       Scarborough   
34         M1E       Scarborough   
35         M4E      East Toronto   
36         M5E  Downtown Toronto   
37         M6E              York   
38         M1G       Scarborough   
39         M4G         East York   
40         M5G  Downtown Toronto   
41         M6G  Downtown Toronto   
42         M1H       Scarborough   
43         M2H        North York   
44         M3H        North York   
45         M3H        North York   
46         M3H        North York   
47         M4H         East York   
48         M5H  Downtown Toronto   
49         M5H  Downtown Toronto   
50         M5H  Downtown Toronto   
51         M6H      West Toronto   
52         M6H      West Toronto   
53         M1J       Scarborough   
54         M2J        North York   
55         M2J        North York   
56         M2J        North York   
57         M3J        North York   
58         M3J        North York   
59         M4J         East York   
60         M5J  Downtown Toronto   
61         M5J  Downtown Toronto   
62         M5J  Downtown Toronto   
63         M6J      West Toronto   
64         M6J      West Toronto   
65         M1K       Scarborough   
66         M1K       Scarborough   
67         M1K       Scarborough   
68         M2K        North York   
69         M3K        North York   
70         M3K        North York   
71         M4K      East Toronto   
72         M4K      East Toronto   
73         M5K  Downtown Toronto   
74         M5K  Downtown Toronto   
75         M6K      West Toronto   
76         M6K      West Toronto   
77         M6K      West Toronto   
78         M1L       Scarborough   
79         M1L       Scarborough   
80         M1L       Scarborough   
81         M2L        North York   
82         M2L        North York   
83         M3L        North York   
84         M4L      East Toronto   
85         M4L      East Toronto   
86         M5L  Downtown Toronto   
87         M5L  Downtown Toronto   
88         M6L        North York   
89         M6L        North York   
90         M6L        North York   
91         M9L        North York   
92         M1M       Scarborough   
93         M1M       Scarborough   
94         M1M       Scarborough   
95         M2M        North York   
96         M2M        North York   
97         M3M        North York   
98         M4M      East Toronto   
99         M5M        North York   
100        M5M        North York   
101        M6M              York   
102        M6M              York   
103        M6M              York   
104        M6M              York   
105        M9M        North York   
106        M9M        North York   
107        M1N       Scarborough   
108        M1N       Scarborough   
109        M2N        North York   
110     

In [213]:
df_a.shape

(210, 3)

In [214]:
#add Geo-spatial data

dfgeo= pd.read_csv("http://cocl.us/Geospatial_data")
dfgeo.rename(columns={'Postal Code':'PostalCode'}, inplace=True)
dfgeo.set_index("PostalCode")

Latitude  Longitude
PostalCode                      
M1B         43.806686 -79.194353
M1C         43.784535 -79.160497
M1E         43.763573 -79.188711
M1G         43.770992 -79.216917
M1H         43.773136 -79.239476
M1J         43.744734 -79.239476
M1K         43.727929 -79.262029
M1L         43.711112 -79.284577
M1M         43.716316 -79.239476
M1N         43.692657 -79.264848
M1P         43.757410 -79.273304
M1R         43.750072 -79.295849
M1S         43.794200 -79.262029
M1T         43.781638 -79.304302
M1V         43.815252 -79.284577
M1W         43.799525 -79.318389
M1X         43.836125 -79.205636
M2H         43.803762 -79.363452
M2J         43.778517 -79.346556
M2K         43.786947 -79.385975
M2L         43.757490 -79.374714
M2M         43.789053 -79.408493
M2N         43.770120 -79.408493
M2P         43.752758 -79.400049
M2R         43.782736 -79.442259
M3A         43.753259 -79.329656
M3B         43.745906 -79.352188
M3C         43.725900 -79.340923
M3H         43.754328 -79.442259
M3J         43.767980 -79.487262
M3K         43.737473 -79.464763
M3L         43.739015 -79.506944
M3M         43.728496 -79.495697
M3N         43.761631 -79.520999
M4A         43.725882 -79.315572
M4B         43.706397 -79.309937
M4C         43.695344 -79.318389
M4E         43.676357 -79.293031
M4G         43.709060 -79.363452
M4H         43.705369 -79.349372
M4J         43.685347 -79.338106
M4K         43.679557 -79.352188
M4L         43.668999 -79.315572
M4M         43.659526 -79.340923
M4N         43.728020 -79.388790
M4P         43.712751 -79.390197
M4R         43.715383 -79.405678
M4S         43.704324 -79.388790
M4T         43.689574 -79.383160
M4V         43.686412 -79.400049
M4W         43.679563 -79.377529
M4X         43.667967 -79.367675
M4Y         43.665860 -79.383160
M5A         43.654260 -79.360636
M5B         43.657162 -79.378937
M5C         43.651494 -79.375418
M5E         43.644771 -79.373306
M5G         43.657952 -79.387383
M5H         43.650571 -79.384568
M5J         43.640816 -79.381752
M5K         43.647177 -79.381576
M5L         43.648198 -79.379817
M5M         43.733283 -79.419750
M5N         43.711695 -79.416936
M5P         43.696948 -79.411307
M5R         43.672710 -79.405678
M5S         43.662696 -79.400049
M5T         43.653206 -79.400049
M5V         43.628947 -79.394420
M5W         43.646435 -79.374846
M5X         43.648429 -79.382280
M6A         43.718518 -79.464763
M6B         43.709577 -79.445073
M6C         43.693781 -79.428191
M6E         43.689026 -79.453512
M6G         43.669542 -79.422564
M6H         43.669005 -79.442259
M6J         43.647927 -79.419750
M6K         43.636847 -79.428191
M6L         43.713756 -79.490074
M6M         43.691116 -79.476013
M6N         43.673185 -79.487262
M6P         43.661608 -79.464763
M6R         43.648960 -79.456325
M6S         43.651571 -79.484450
M7A         43.662301 -79.389494
M7R         43.636966 -79.615819
M7Y         43.662744 -79.321558
M8V         43.605647 -79.501321
M8W         43.602414 -79.543484
M8X         43.653654 -79.506944
M8Y         43.636258 -79.498509
M8Z         43.628841 -79.520999
M9A         43.667856 -79.532242
M9B         43.650943 -79.554724
M9C         43.643515 -79.577201
M9L         43.756303 -79.565963
M9M         43.724766 -79.532242
M9N         43.706876 -79.518188
M9P         43.696319 -79.532242
M9R         43.688905 -79.554724
M9V         43.739416 -79.588437
M9W         43.706748 -79.594054

In [215]:
def get_geocode(postal_code):
    # initialize your variable to None
    lat_lng_coords = None
    while(lat_lng_coords is None):
        g = geocoder.google('{}, Toronto, Ontario'.format(postal_code))
        lat_lng_coords = g.latlng
    latitude = lat_lng_coords[0]
    longitude = lat_lng_coords[1]
    return latitude,longitude

In [216]:
df_a.set_index("PostalCode")
toronto_data=pd.merge(df_a, dfgeo)
toronto_data.head()

PostalCode           Borough     Neighbourhood   Latitude  Longitude
0        M3A        North York         Parkwoods  43.753259 -79.329656
1        M4A        North York  Victoria Village  43.725882 -79.315572
2        M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3        M6A        North York  Lawrence Heights  43.718518 -79.464763
4        M6A        North York    Lawrence Manor  43.718518 -79.464763

In [217]:
#remove the duplication
df = df.loc[:,~df.columns.duplicated()]
df

PostalCode           Borough  \
0          M3A        North York   
1          M4A        North York   
2          M5A  Downtown Toronto   
3          M6A        North York   
4          M6A        North York   
5          M7A  Downtown Toronto   
6          M9A      Queen's Park   
7          M1B       Scarborough   
8          M1B       Scarborough   
9          M3B        North York   
10         M4B         East York   
11         M4B         East York   
12         M5B  Downtown Toronto   
13         M5B  Downtown Toronto   
14         M6B        North York   
15         M9B         Etobicoke   
16         M9B         Etobicoke   
17         M9B         Etobicoke   
18         M9B         Etobicoke   
19         M9B         Etobicoke   
20         M1C       Scarborough   
21         M1C       Scarborough   
22         M1C       Scarborough   
23         M3C        North York   
24         M3C        North York   
25         M4C         East York   
26         M5C  Downtown Toronto   
27         M6C              York   
28         M9C         Etobicoke   
29         M9C         Etobicoke   
30         M9C         Etobicoke   
31         M9C         Etobicoke   
32         M1E       Scarborough   
33         M1E       Scarborough   
34         M1E       Scarborough   
35         M4E      East Toronto   
36         M5E  Downtown Toronto   
37         M6E              York   
38         M1G       Scarborough   
39         M4G         East York   
40         M5G  Downtown Toronto   
41         M6G  Downtown Toronto   
42         M1H       Scarborough   
43         M2H        North York   
44         M3H        North York   
45         M3H        North York   
46         M3H        North York   
47         M4H         East York   
48         M5H  Downtown Toronto   
49         M5H  Downtown Toronto   
50         M5H  Downtown Toronto   
51         M6H      West Toronto   
52         M6H      West Toronto   
53         M1J       Scarborough   
54         M2J        North York   
55         M2J        North York   
56         M2J        North York   
57         M3J        North York   
58         M3J        North York   
59         M4J         East York   
60         M5J  Downtown Toronto   
61         M5J  Downtown Toronto   
62         M5J  Downtown Toronto   
63         M6J      West Toronto   
64         M6J      West Toronto   
65         M1K       Scarborough   
66         M1K       Scarborough   
67         M1K       Scarborough   
68         M2K        North York   
69         M3K        North York   
70         M3K        North York   
71         M4K      East Toronto   
72         M4K      East Toronto   
73         M5K  Downtown Toronto   
74         M5K  Downtown Toronto   
75         M6K      West Toronto   
76         M6K      West Toronto   
77         M6K      West Toronto   
78         M1L       Scarborough   
79         M1L       Scarborough   
80         M1L       Scarborough   
81         M2L        North York   
82         M2L        North York   
83         M3L        North York   
84         M4L      East Toronto   
85         M4L      East Toronto   
86         M5L  Downtown Toronto   
87         M5L  Downtown Toronto   
88         M6L        North York   
89         M6L        North York   
90         M6L        North York   
91         M9L        North York   
92         M1M       Scarborough   
93         M1M       Scarborough   
94         M1M       Scarborough   
95         M2M        North York   
96         M2M        North York   
97         M3M        North York   
98         M4M      East Toronto   
99         M5M        North York   
100        M5M        North York   
101        M6M              York   
102        M6M              York   
103        M6M              York   
104        M6M              York   
105        M9M        North York   
106        M9M        North York   
107        M1N       Scarborough   
108        M1N       Scarborough   
109        M2N        North York   
110     

In [218]:
# to see Borough of Toronto and their neighbourhood

todef_data=toronto_data[toronto_data['Borough'].str.contains("Toronto")]
todef_data

PostalCode           Borough  \
2          M5A  Downtown Toronto   
5          M7A  Downtown Toronto   
12         M5B  Downtown Toronto   
13         M5B  Downtown Toronto   
26         M5C  Downtown Toronto   
35         M4E      East Toronto   
36         M5E  Downtown Toronto   
40         M5G  Downtown Toronto   
41         M6G  Downtown Toronto   
48         M5H  Downtown Toronto   
49         M5H  Downtown Toronto   
50         M5H  Downtown Toronto   
51         M6H      West Toronto   
52         M6H      West Toronto   
60         M5J  Downtown Toronto   
61         M5J  Downtown Toronto   
62         M5J  Downtown Toronto   
63         M6J      West Toronto   
64         M6J      West Toronto   
71         M4K      East Toronto   
72         M4K      East Toronto   
73         M5K  Downtown Toronto   
74         M5K  Downtown Toronto   
75         M6K      West Toronto   
76         M6K      West Toronto   
77         M6K      West Toronto   
84         M4L      East Toronto   
85         M4L      East Toronto   
86         M5L  Downtown Toronto   
87         M5L  Downtown Toronto   
98         M4M      East Toronto   
111        M4N   Central Toronto   
112        M5N   Central Toronto   
120        M4P   Central Toronto   
121        M5P   Central Toronto   
122        M5P   Central Toronto   
123        M6P      West Toronto   
124        M6P      West Toronto   
129        M4R   Central Toronto   
130        M5R   Central Toronto   
131        M5R   Central Toronto   
132        M5R   Central Toronto   
133        M6R      West Toronto   
134        M6R      West Toronto   
141        M4S   Central Toronto   
142        M5S  Downtown Toronto   
143        M5S  Downtown Toronto   
144        M6S      West Toronto   
145        M6S      West Toronto   
149        M4T   Central Toronto   
150        M4T   Central Toronto   
151        M5T  Downtown Toronto   
152        M5T  Downtown Toronto   
153        M5T  Downtown Toronto   
158        M4V   Central Toronto   
159        M4V   Central Toronto   
160        M4V   Central Toronto   
161        M4V   Central Toronto   
162        M4V   Central Toronto   
163        M5V  Downtown Toronto   
164        M5V  Downtown Toronto   
165        M5V  Downtown Toronto   
166        M5V  Downtown Toronto   
167        M5V  Downtown Toronto   
168        M5V  Downtown Toronto   
169        M5V  Downtown Toronto   
182        M4W  Downtown Toronto   
183        M5W  Downtown Toronto   
188        M4X  Downtown Toronto   
189        M4X  Downtown Toronto   
190        M5X  Downtown Toronto   
191        M5X  Downtown Toronto   
195        M4Y  Downtown Toronto   
196        M7Y      East Toronto   

                                         Neighbourhood   Latitude  Longitude  
2                                         Harbourfront  43.654260 -79.360636  
5                                         Queen's Park  43.662301 -79.389494  
12                                             Ryerson  43.657162 -79.378937  
13                                     Garden District  43.657162 -79.378937  
26                                      St. James Town  43.651494 -79.375418  
35                                         The Beaches  43.676357 -79.293031  
36                                         Berczy Park  43.644771 -79.373306  
40                                  Central Bay Street  43.657952 -79.387383  
41                                            Christie  43.669542 -79.422564  
48                                            Adelaide  43.650571 -79.384568  
49                                                King  43.650571 -79.384568  
50                                            Richmond  43.650571 -79.384568  
51                                  Dovercourt Village  43.669005 -79.442259  
52                                            Dufferin  43.669005 -79.442259  
60                                   Harbourfront East  43.640816 -79.381752  
61                                     

# In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent toronto_explorer, as shown below.

address = 'Toronto, Canada'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto, Canada are {}, {}.'.format(latitude, longitude))

Create a map of Toronto with neighborhoods superimposed on top

In [219]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighbourhood in zip(toronto_data['Latitude'], toronto_data['Longitude'], toronto_data['Borough'], toronto_data['Neighbourhood']):
    label = '{}, {}'.format(neighbourhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='green',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

### Define Foursquare Credentials and Version

In [220]:
CLIENT_ID = 'IGFAY3CHU0CGOTDGFOYL2M4TAFFM2RA0DU1E0JBHYNVF4PLH' # your Foursquare ID
CLIENT_SECRET = 'WNF4IBUV3DFOLHYBLNJRTDXOAWIXL3T3OZHUBH1DIOAELQEY' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: IGFAY3CHU0CGOTDGFOYL2M4TAFFM2RA0DU1E0JBHYNVF4PLH
CLIENT_SECRET:WNF4IBUV3DFOLHYBLNJRTDXOAWIXL3T3OZHUBH1DIOAELQEY


### Explore the first neighborhood

In [221]:
toronto_data.loc[0, 'Neighbourhood']
neighbourhood_latitude = toronto_data.loc[0, 'Latitude']
neighbourhood_longitude = toronto_data.loc[0, 'Longitude']

neighbourhood_name = toronto_data.loc[0, 'Neighbourhood'] 
print('Latitude and longitude values of {} are {}, {}.'.format(neighbourhood_name, 
                                                               neighbourhood_latitude, 
                                                               neighbourhood_longitude))

Latitude and longitude values of Parkwoods are 43.7532586, -79.3296565.


### 100 venues that are in Parkwoods within a radius of 500 meters.

In [222]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius
# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?&client_id=IGFAY3CHU0CGOTDGFOYL2M4TAFFM2RA0DU1E0JBHYNVF4PLH&client_secret=WNF4IBUV3DFOLHYBLNJRTDXOAWIXL3T3OZHUBH1DIOAELQEY&v=20180605&ll=43.7532586,-79.3296565&radius=500&limit=100'

In [223]:
# get the result
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e3c755771c428001b72a816'},
 'response': {'warning': {'text': "There aren't a lot of results near you. Try something more general, reset your filters, or expand the search area."},
  'headerLocation': 'Parkwoods - Donalda',
  'headerFullLocation': 'Parkwoods - Donalda, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 2,
  'suggestedBounds': {'ne': {'lat': 43.757758604500005,
    'lng': -79.32343823984928},
   'sw': {'lat': 43.7487585955, 'lng': -79.33587476015072}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4e8d9dcdd5fbbbb6b3003c7b',
       'name': 'Brookbanks Park',
       'location': {'address': 'Toronto',
        'lat': 43.751976046055574,
        'lng': -79.33214044722958,
        'labeledLatLngs': 

In [224]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

### clean the json and structure it into a pandas dataframe

In [232]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name         categories        lat        lng
0  Brookbanks Park               Park  43.751976 -79.332140
1    Variety Store  Food & Drink Shop  43.751974 -79.333114

In [233]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

2 venues were returned by Foursquare.


### Explore Neighborhoods in Toronto

In [235]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]["groups"][0]["items"]
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [236]:
toronto_venues = getNearbyVenues(names=toronto_data['Neighbourhood'],
                                   latitudes=toronto_data['Latitude'],
                                   longitudes=toronto_data['Longitude']
                                  )

Parkwoods
Victoria Village
Harbourfront
Lawrence Heights
Lawrence Manor
Queen's Park
Queen's Park
Rouge
Malvern
Don Mills North
Woodbine Gardens
Parkview Hill
Ryerson
Garden District
Glencairn
Cloverdale
Islington
Martin Grove
Princess Gardens
West Deane Park
Highland Creek
Rouge Hill
Port Union
Flemingdon Park
Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Bloordale Gardens
Eringate
Markland Wood
Old Burnhamthorpe
Guildwood
Morningside
West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor
Downsview North
Wilson Heights
Thorncliffe Park
Adelaide
King
Richmond
Dovercourt Village
Dufferin
Scarborough Village
Fairview
Henry Farm
Oriole
Northwood Park
York University
East Toronto
Harbourfront East
Toronto Islands
Union Station
Little Portugal
Trinity
East Birchmount Park
Ionview
Kennedy Park
Bayview Village
CFB Toronto
Downsview East
The Danforth West
Riverdale
Design Exchange
Toronto 

In [237]:
# check size of dataframe
print(toronto_venues.shape)
toronto_venues.head()

(4320, 7)


Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0         Parkwoods               43.753259               -79.329656   
1         Parkwoods               43.753259               -79.329656   
2  Victoria Village               43.725882               -79.315572   
3  Victoria Village               43.725882               -79.315572   
4  Victoria Village               43.725882               -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3             Tim Hortons       43.725517       -79.313103   
4               Portugril       43.725819       -79.312785   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3            Coffee Shop  
4  Portuguese Restaurant

In [238]:
# number of venues that returned on each neighbourhood
toronto_venues.groupby('Neighbourhood').count()

Neighbourhood Latitude  \
Neighbourhood                                                               
Adelaide                                                              100   
Agincourt                                                               4   
Agincourt North                                                         2   
Albion Gardens                                                         12   
Alderwood                                                               9   
Bathurst Manor                                                         22   
Bathurst Quay                                                          16   
Bayview Village                                                         4   
Beaumond Heights                                                       12   
Bedford Park                                                           23   
Berczy Park                                                            54   
Birch Cliff                                                             4   
Bloordale Gardens                                                       9   
Brockton                                                               23   
Business Reply Mail Processing Centre 969 Eastern                      18   
CFB Toronto                                                             3   
CN Tower                                                               16   
Cabbagetown                                                            41   
Caledonia-Fairbanks                                                     5   
Canada Post Gateway Processing Centre                                  11   
Cedarbrae                                                               8   
Central Bay Street                                                     85   
Chinatown                                                              84   
Christie                                                               18   
Church and Wellesley                                                   82   
Clairlea                                                                9   
Clarks Corners                                                         12   
Cliffcrest                                                              3   
Cliffside                                                               3   
Cliffside West                                                          4   
Cloverdale                                                              1   
Commerce Court                                                        100   
Davisville                                                             37   
Davisville North                                                        6   
Deer Park                                                              14   
Del Ray                                                                 5   
Design Exchange                                                       100   
Don Mills North                                                         4   
Don Mills South                                                        22   
Dorset Park                                                             6   
Dovercourt Village                                                     20   
Downsview                                                               4   
Downsview Central                                                       3   
Downsview East                                                          3   
Downsview North                                                        22   
Downsview Northwest                                                     4   
Downsview West                                                          5   
Dufferin                                                               20   
East Birchmount Park                                                    5   
East Toronto                                                            4   
Emery                                          

In [239]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 266 uniques categories.


## Analyse Each Neighbourhood

In [240]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighbourhood column back to dataframe
toronto_onehot['Neighbourhood'] = toronto_venues['Neighbourhood'] 

# move neighbourhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Neighbourhood  Accessories Store  Afghan Restaurant  Airport  \
0         Parkwoods                  0                  0        0   
1         Parkwoods                  0                  0        0   
2  Victoria Village                  0                  0        0   
3  Victoria Village                  0                  0        0   
4  Victoria Village                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                    0                 0                   0            0   
1                    0                 0                   0            0   
2                    0                 0                   0            0   
3                    0                 0                   0            0   
4                    0                 0                   0            0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0              0          0           0           0       0     0    0   
1              0          0           0           0       0     0    0   
2              0          0           0           0       0     0    0   
3              0          0           0           0       0     0    0   
4              0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Basketball Stadium  \
0               0                 0                 0                   0   
1               0                 0                 0                   0   
2               0                 0                 0                   0   
3               0                 0                 0                   0   
4               0                 0                 0                   0   

   Beach  Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  \
0      0                0         0           0                   0   
1      0                0         0           0                   0   
2      0                0         0           0                   0   
3      0                0         0           0                   0   
4      0                0         0           0                   0   

   Bike Shop  Bistro  Boat or Ferry  Bookstore  Boutique  \
0          0       0              0          0         0   
1          0       0              0          0         0   
2          0       0              0          0         0   
3          0       0              0          0         0   
4          0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0         0             0  

In [241]:
toronto_onehot.shape

(4320, 267)

### group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [242]:
toronto_grouped = toronto_onehot.groupby('Neighbourhood').mean().reset_index()
toronto_grouped

Neighbourhood  Accessories Store  \
0                                             Adelaide           0.000000   
1                                            Agincourt           0.000000   
2                                      Agincourt North           0.000000   
3                                       Albion Gardens           0.000000   
4                                            Alderwood           0.000000   
5                                       Bathurst Manor           0.000000   
6                                        Bathurst Quay           0.000000   
7                                      Bayview Village           0.000000   
8                                     Beaumond Heights           0.000000   
9                                         Bedford Park           0.000000   
10                                         Berczy Park           0.000000   
11                                         Birch Cliff           0.000000   
12                                   Bloordale Gardens           0.000000   
13                                            Brockton           0.000000   
14   Business Reply Mail Processing Centre 969 Eastern           0.000000   
15                                         CFB Toronto           0.000000   
16                                            CN Tower           0.000000   
17                                         Cabbagetown           0.000000   
18                                 Caledonia-Fairbanks           0.000000   
19               Canada Post Gateway Processing Centre           0.000000   
20                                           Cedarbrae           0.000000   
21                                  Central Bay Street           0.000000   
22                                           Chinatown           0.000000   
23                                            Christie           0.000000   
24                                Church and Wellesley           0.000000   
25                                            Clairlea           0.000000   
26                                      Clarks Corners           0.000000   
27                                          Cliffcrest           0.000000   
28                                           Cliffside           0.000000   
29                                      Cliffside West           0.000000   
30                                          Cloverdale           0.000000   
31                                      Commerce Court           0.000000   
32                                          Davisville           0.000000   
33                                    Davisville North           0.000000   
34                                           Deer Park           0.000000   
35                                             Del Ray           0.000000   
36                                     Design Exchange           0.000000   
37                                     Don Mills North           0.000000   
38                                     Don Mills South           0.000000   
39                                         Dorset Park           0.000000   
40                                  Dovercourt Village           0.000000   
41                                           Downsview           0.000000   
42                                   Downsview Central           0.000000   
43                                      Downsview East           0.000000   
44                                     Downsview North           0.000000   
45                                 Downsview Northwest           0.000000   
46                                      Downsview West           0.000000   
47                                            Dufferin           0.000000   
48                                East Birchmount Park           0.000000   
49                                        East Toronto           0.000000   
50                                               Emery           0.000000   
51                                   

In [243]:
toronto_grouped.shape

(203, 267)

### print each neighborhood along with the top 5 most common venues

In [244]:
num_top_venues = 5

for hood in toronto_grouped['Neighbourhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighbourhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
         venue  freq
0  Coffee Shop  0.07
1         Café  0.04
2          Bar  0.04
3   Steakhouse  0.04
4       Bakery  0.03


----Agincourt----
                       venue  freq
0                     Lounge  0.25
1             Breakfast Spot  0.25
2  Latin American Restaurant  0.25
3               Skating Rink  0.25
4  Middle Eastern Restaurant  0.00


----Agincourt North----
                             venue  freq
0                       Playground   0.5
1                             Park   0.5
2               Mexican Restaurant   0.0
3              Monument / Landmark   0.0
4  Molecular Gastronomy Restaurant   0.0


----Albion Gardens----
           venue  freq
0    Pizza Place  0.17
1  Grocery Store  0.17
2       Pharmacy  0.08
3    Coffee Shop  0.08
4     Beer Store  0.08


----Alderwood----
            venue  freq
0     Pizza Place  0.22
1     Coffee Shop  0.11
2    Skating Rink  0.11
3  Sandwich Place  0.11
4    Dance Studio  0.11


----Bathurst Manor----
   

### put that into a pandas dataframe

In [245]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [246]:
# create the new dataframe and display the top 10 venues for each neighborhood.

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighbourhoods_venues_sorted = pd.DataFrame(columns=columns)
neighbourhoods_venues_sorted['Neighbourhood'] = toronto_grouped['Neighbourhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighbourhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighbourhoods_venues_sorted.head()

Neighbourhood 1st Most Common Venue      2nd Most Common Venue  \
0         Adelaide           Coffee Shop                       Café   
1        Agincourt                Lounge  Latin American Restaurant   
2  Agincourt North            Playground                       Park   
3   Albion Gardens           Pizza Place              Grocery Store   
4        Alderwood           Pizza Place                   Pharmacy   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                   Bar            Steakhouse            Restaurant   
1        Breakfast Spot          Skating Rink             Drugstore   
2           Yoga Studio            Donut Shop    Dim Sum Restaurant   
3        Sandwich Place  Fast Food Restaurant            Beer Store   
4          Skating Rink        Sandwich Place                   Pub   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0        Cosmetics Shop                Bakery        Breakfast Spot   
1                 Diner        Discount Store               Dog Run   
2                 Diner        Discount Store               Dog Run   
3   Japanese Restaurant        Discount Store   Fried Chicken Joint   
4          Dance Studio           Coffee Shop                   Gym   

  9th Most Common Venue 10th Most Common Venue  
0      Asian Restaurant        Thai Restaurant  
1      Doner Restaurant             Donut Shop  
2      Doner Restaurant    Dumpling Restaurant  
3              Pharmacy            Coffee Shop  
4   Dumpling Restaurant              Drugstore

## Cluster Neighbourhoods

In [249]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([1, 1, 0, 1, 1, 1, 1, 1, 1, 1], dtype=int32)

In [250]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

toronto_merged = toronto_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighbourhoods_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')

toronto_merged.head() # check the last columns!

PostalCode           Borough     Neighbourhood   Latitude  Longitude  \
0        M3A        North York         Parkwoods  43.753259 -79.329656   
1        M4A        North York  Victoria Village  43.725882 -79.315572   
2        M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636   
3        M6A        North York  Lawrence Heights  43.718518 -79.464763   
4        M6A        North York    Lawrence Manor  43.718518 -79.464763   

   Cluster Labels 1st Most Common Venue   2nd Most Common Venue  \
0             0.0                  Park       Food & Drink Shop   
1             1.0           Pizza Place            Hockey Arena   
2             1.0           Coffee Shop                  Bakery   
3             1.0        Clothing Store  Furniture / Home Store   
4             1.0        Clothing Store  Furniture / Home Store   

  3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
0           Yoga Studio             Donut Shop    Dim Sum Restaurant   
1           Coffee Shop  Portuguese Restaurant          Dessert Shop   
2                   Pub                   Café                  Park   
3     Accessories Store          Women's Store              Boutique   
4     Accessories Store          Women's Store              Boutique   

  6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
0                 Diner         Discount Store               Dog Run   
1    Dim Sum Restaurant                  Diner        Discount Store   
2        Breakfast Spot     Mexican Restaurant           Yoga Studio   
3    Miscellaneous Shop  Vietnamese Restaurant           Event Space   
4    Miscellaneous Shop  Vietnamese Restaurant           Event Space   

  9th Most Common Venue 10th Most Common Venue  
0      Doner Restaurant              Drugstore  
1               Dog Run       Doner Restaurant  
2     French Restaurant             Restaurant  
3           Coffee Shop    Sporting Goods Shop  
4           Coffee Shop    Sporting Goods Shop

In [251]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighbourhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        #color=rainbow[cluster-1],
        fill=True,
        #fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Examine Clusters

#### Cluster 1

In [264]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
0          North York             0.0                  Park   
37               York             0.0                  Park   
53        Scarborough             0.0            Playground   
59          East York             0.0                  Park   
69         North York             0.0               Airport   
70         North York             0.0               Airport   
88         North York             0.0      Basketball Court   
89         North York             0.0      Basketball Court   
90         North York             0.0      Basketball Court   
111   Central Toronto             0.0                Lawyer   
119        North York             0.0                  Park   
121   Central Toronto             0.0                  Park   
122   Central Toronto             0.0                  Park   
149   Central Toronto             0.0           Summer Camp   
150   Central Toronto             0.0           Summer Camp   
154       Scarborough             0.0            Playground   
155       Scarborough             0.0            Playground   
156       Scarborough             0.0            Playground   
157       Scarborough             0.0            Playground   
182  Downtown Toronto             0.0                  Park   
192         Etobicoke             0.0                  Park   
193         Etobicoke             0.0                  Park   
194         Etobicoke             0.0                  Park   

    2nd Most Common Venue 3rd Most Common Venue       4th Most Common Venue  \
0       Food & Drink Shop           Yoga Studio                  Donut Shop   
37          Women's Store  Fast Food Restaurant                      Market   
53            Yoga Studio            Donut Shop                Dessert Shop   
59      Convenience Store           Coffee Shop                   Drugstore   
69                   Park           Snack Place                 Yoga Studio   
70                   Park           Snack Place                 Yoga Studio   
88                   Park                Bakery  Construction & Landscaping   
89                   Park                Bakery  Construction & Landscaping   
90                   Park                Bakery  Construction & Landscaping   
111                  Park              Bus Line                 Swim School   
119                  Bank     Electronics Store           Convenience Store   
121      Sushi Restaurant         Jewelry Store                       Trail   
122      Sushi Restaurant         Jewelry Store                       Trail   
149            Playground           Yoga Studio          Dim Sum Restaurant   
150            Playground           Yoga Studio          Dim Sum Restaurant   
154                  Park           Yoga Studio                  Donut Shop   
155                  Park           Yoga Studio                  Donut Shop   
156                  Park           Yoga Studio                  Donut Shop   
157                  Park           Yoga Studio                  Donut Shop   
182            Playground                 Trail                 Yoga Studio   
192                 River            Smoke Shop                 Yoga Studio   
193                 River            Smoke Shop                 Yoga Studio   
194                 River            Smoke Shop                 Yoga Studio   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0      Dim Sum Restaurant                 Diner        Discount Store   
37              Drugstore                 Diner        Discount Store   
53     Dim Sum Restaurant                 Diner        Discount Store   
59     Dim Sum Restaurant                 Diner        Discount Store   
69             Donut Shop    Dim Sum Restaurant                 Diner   
70             Donut Shop    Dim Sum Restaurant                 Diner   
88            Yoga Studio        Discount Store               Dog Run   
89            Yoga S

#### Cluster 2

In [265]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels      1st Most Common Venue  \
1          North York             1.0                Pizza Place   
2    Downtown Toronto             1.0                Coffee Shop   
3          North York             1.0             Clothing Store   
4          North York             1.0             Clothing Store   
5    Downtown Toronto             1.0                Coffee Shop   
6        Queen's Park             1.0                Coffee Shop   
7         Scarborough             1.0       Fast Food Restaurant   
8         Scarborough             1.0       Fast Food Restaurant   
9          North York             1.0       Gym / Fitness Center   
10          East York             1.0                Pizza Place   
11          East York             1.0                Pizza Place   
12   Downtown Toronto             1.0                Coffee Shop   
13   Downtown Toronto             1.0                Coffee Shop   
14         North York             1.0                        Pub   
23         North York             1.0                 Beer Store   
24         North York             1.0                 Beer Store   
25          East York             1.0                       Park   
26   Downtown Toronto             1.0                Coffee Shop   
27               York             1.0               Hockey Arena   
28          Etobicoke             1.0                Pizza Place   
29          Etobicoke             1.0                Pizza Place   
30          Etobicoke             1.0                Pizza Place   
31          Etobicoke             1.0                Pizza Place   
32        Scarborough             1.0                Pizza Place   
33        Scarborough             1.0                Pizza Place   
34        Scarborough             1.0                Pizza Place   
35       East Toronto             1.0                Pizza Place   
36   Downtown Toronto             1.0                Coffee Shop   
38        Scarborough             1.0                Coffee Shop   
39          East York             1.0        Sporting Goods Shop   
40   Downtown Toronto             1.0                Coffee Shop   
41   Downtown Toronto             1.0              Grocery Store   
42        Scarborough             1.0                       Bank   
43         North York             1.0   Mediterranean Restaurant   
44         North York             1.0                Coffee Shop   
45         North York             1.0                Coffee Shop   
46         North York             1.0                Coffee Shop   
47          East York             1.0          Indian Restaurant   
48   Downtown Toronto             1.0                Coffee Shop   
49   Downtown Toronto             1.0                Coffee Shop   
50   Downtown Toronto             1.0                Coffee Shop   
51       West Toronto             1.0                   Pharmacy   
52       West Toronto             1.0                   Pharmacy   
54         North York             1.0             Clothing Store   
55         North York             1.0             Clothing Store   
56         North York             1.0             Clothing Store   
57         North York             1.0         Falafel Restaurant   
58         North York             1.0         Falafel Restaurant   
60   Downtown Toronto             1.0                Coffee Shop   
61   Downtown Toronto             1.0                Coffee Shop   
62   Downtown Toronto             1.0                Coffee Shop   
63       West Toronto             1.0                        Bar   
64       West Toronto             1.0                        Bar   
65        Scarborough             1.0             Discount Store   
66        Scarborough             1.0             Discount Store   
67        Scarborough             1.0             Discount Store   
68         North York             1.0                       Café   
71       East Toronto             1.0           Greek Restaurant   
72

#### Cluster 3

In [257]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
15  Etobicoke             2.0           Golf Course           Yoga Studio   
16  Etobicoke             2.0           Golf Course           Yoga Studio   
17  Etobicoke             2.0           Golf Course           Yoga Studio   
18  Etobicoke             2.0           Golf Course           Yoga Studio   
19  Etobicoke             2.0           Golf Course           Yoga Studio   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
15             Drugstore    Dim Sum Restaurant                 Diner   
16             Drugstore    Dim Sum Restaurant                 Diner   
17             Drugstore    Dim Sum Restaurant                 Diner   
18             Drugstore    Dim Sum Restaurant                 Diner   
19             Drugstore    Dim Sum Restaurant                 Diner   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
15        Discount Store               Dog Run      Doner Restaurant   
16        Discount Store               Dog Run      Doner Restaurant   
17        Discount Store               Dog Run      Doner Restaurant   
18        Discount Store               Dog Run      Doner Restaurant   
19        Discount Store               Dog Run      Doner Restaurant   

   9th Most Common Venue 10th Most Common Venue  
15            Donut Shop    Dumpling Restaurant  
16            Donut Shop    Dumpling Restaurant  
17            Donut Shop    Dumpling Restaurant  
18            Donut Shop    Dumpling Restaurant  
19            Donut Shop    Dumpling Restaurant

#### Cluster 4

In [256]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
97   North York             3.0      Business Service            Food Truck   
105  North York             3.0        Baseball Field           Yoga Studio   
106  North York             3.0        Baseball Field           Yoga Studio   
197   Etobicoke             3.0      Business Service        Baseball Field   
198   Etobicoke             3.0      Business Service        Baseball Field   
199   Etobicoke             3.0      Business Service        Baseball Field   
200   Etobicoke             3.0      Business Service        Baseball Field   
201   Etobicoke             3.0      Business Service        Baseball Field   
202   Etobicoke             3.0      Business Service        Baseball Field   
203   Etobicoke             3.0      Business Service        Baseball Field   
204   Etobicoke             3.0      Business Service        Baseball Field   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
97         Baseball Field           Yoga Studio            Donut Shop   
105             Drugstore                 Diner        Discount Store   
106             Drugstore                 Diner        Discount Store   
197           Yoga Studio             Drugstore        Discount Store   
198           Yoga Studio             Drugstore        Discount Store   
199           Yoga Studio             Drugstore        Discount Store   
200           Yoga Studio             Drugstore        Discount Store   
201           Yoga Studio             Drugstore        Discount Store   
202           Yoga Studio             Drugstore        Discount Store   
203           Yoga Studio             Drugstore        Discount Store   
204           Yoga Studio             Drugstore        Discount Store   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
97         Discount Store               Dog Run      Doner Restaurant   
105               Dog Run      Doner Restaurant            Donut Shop   
106               Dog Run      Doner Restaurant            Donut Shop   
197               Dog Run      Doner Restaurant            Donut Shop   
198               Dog Run      Doner Restaurant            Donut Shop   
199               Dog Run      Doner Restaurant            Donut Shop   
200               Dog Run      Doner Restaurant            Donut Shop   
201               Dog Run      Doner Restaurant            Donut Shop   
202               Dog Run      Doner Restaurant            Donut Shop   
203               Dog Run      Doner Restaurant            Donut Shop   
204               Dog Run      Doner Restaurant            Donut Shop   

    9th Most Common Venue 10th Most Common Venue  
97              Drugstore         Farmers Market  
105   Dumpling Restaurant   Fast Food Restaurant  
106   Dumpling Restaurant   Fast Food Restaurant  
197   Dumpling Restaurant   Fast Food Restaurant  
198   Dumpling Restaurant   Fast Food Restaurant  
199   Dumpling Restaurant   Fast Food Restaurant  
200   Dumpling Restaurant   Fast Food Restaurant  
201   Dumpling Restaurant   Fast Food Restaurant  
202   Dumpling Restaurant   Fast Food Restaurant  
203   Dumpling Restaurant   Fast Food Restaurant  
204   Dumpling Restaurant   Fast Food Restaurant

#### Cluster 5

In [258]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
20  Scarborough             4.0                   Bar           Yoga Studio   
21  Scarborough             4.0                   Bar           Yoga Studio   
22  Scarborough             4.0                   Bar           Yoga Studio   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
20             Drugstore                 Diner        Discount Store   
21             Drugstore                 Diner        Discount Store   
22             Drugstore                 Diner        Discount Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
20               Dog Run      Doner Restaurant            Donut Shop   
21               Dog Run      Doner Restaurant            Donut Shop   
22               Dog Run      Doner Restaurant            Donut Shop   

   9th Most Common Venue 10th Most Common Venue  
20   Dumpling Restaurant   Fast Food Restaurant  
21   Dumpling Restaurant   Fast Food Restaurant  
22   Dumpling Restaurant   Fast Food Restaurant